# Visualizando a COVID-19 no RN
> Evolução e estágio atual dos municípios

- toc: true 
- badges: true
- hide_binder_badge: true
- comments: true
- categories: [colab]
- image: images/rn.png

> Caso esteja visualizando este post em um dispositivo móvel, por favor utilize seu dispositivo na horizontal.

Este post reúne análises das ocorrências de COVID-19 nos municípios do Rio Grande do Norte. Todos os municípios apresentados nesta análise tiveram casos suspeitos de COVID-19. Os dados utilizados para análise são fornecidos pela [Secretaria de Saúde Pública](http://www.saude.rn.gov.br/Conteudo.asp?TRAN=ITEM&TARG=223456&ACT=&PAGE=&PARM=&LBL=MAT%C9RIA).

A análise inicial se concentra nos municípios que apresentam os maiores valores para cada métrica analisada. Esta análise apresenta diferentes métricas, tanto absolutas (suspeitos, confirmados e mortes) quanto relativas (confirmados e mortes por 100 mil habitantes). 

> Sempre que alternar entre tipos de métrica, clique duas vezes na área principal do gráfico para que o zoom se ajuste (a área principal do gráfico tem pano de fundo quadriculado).

A análise seguinte se concentra nos municípios de maior população (em geral ou em relação à sua microregião). Além disso, apresentamos a análise por dia e em dias decorridos desde o primeiro caso.

> Sempre que alternar entre tipos de métrica, clique duas vezes na área principal do gráfico para que o zoom se ajuste (a área principal do gráfico tem pano de fundo quadriculado).

A análise final apresenta casos suspeitos e confirmados e usa georeferenciamento para visualizar a trajetória do vírus pelo RN. Nesta análise, apresentamos tanto a evolução dos casos confirmados como das mortes. Nos mapas, é possível visualizar informações sobre cada localidade passando o mouse por cima do município desejado.

> É possível animar a linha do tempo da evolução dos casos apertando o botão play, ou visualizar uma data específica usando o slider.

Em cada gráfico, várias outras opções de interação estão disponíveis, podendo ser exploradas pelo menu que aparece no canto superior direito de cada um.

In [1]:
#hide
!pip install -U pandas
!pip install -U plotly
!pip install -U plotly-express

     |████████████████████████████████| 10.5MB 4.5MB/s 
ERROR: google-colab 1.0.0 has requirement pandas~=1.0.0; python_version >= "3.0", but you'll have pandas 1.1.0 which is incompatible.
  Found existing installation: pandas 1.0.5
    Uninstalling pandas-1.0.5:
      Successfully uninstalled pandas-1.0.5


     |████████████████████████████████| 12.9MB 305kB/s 
  Found existing installation: plotly 4.4.1
    Uninstalling plotly-4.4.1:
      Successfully uninstalled plotly-4.4.1


In [1]:
#hide
localidades = [
                "Mossoró",            
                "Apodi",
                "Açu",
                "Pau dos Ferros",
                "Macau",
                "Angicos",
                "Lajes",
                "Caicó",
                "Currais Novos",
                "João Câmara",
                "Santa Cruz",
                "Nova Cruz",
                "São Paulo do Potengi",
                "Touros",
                "Areia Branca",
                "Baraúna",
                "Santo Antônio",
                "São Miguel",
                "Lagoa Nova",
                "Santana do Matos",
                "Patu",
                "Upanema",

                "Natal",
                "Extremoz",
                "Parnamirim",
                "Ceará-mirim",
                "Macaíba",
                "Nísia Floresta",
                "Goianinha",
                "São Gonçalo do Amarante",
                "São José de Mipibu",
]

In [2]:
#hide
import requests
import datetime
from urllib.error import HTTPError

import pandas as pd
import numpy as np
import plotly.express as px


# base variables
initial_date = datetime.date(2020,2,28)
days_elapsed = (datetime.date.today() - initial_date).days + 1
base_url = "https://raw.githubusercontent.com/leobezerra/covid19/master/data/rn_covid_19_boletins"

# dicts for data collection
dates = (f"{(initial_date + datetime.timedelta(days=days)).strftime('%m-%d-%Y')}" for days in range(0, days_elapsed))
csvs = {f"{day}": f"{base_url}/{day}.csv" for day in dates}

# collecting data
dfs = []
for day, url in csvs.items():
    try:
        dfs.append(pd.read_csv(url)) 
    except HTTPError:
        pass
df = pd.concat(dfs)

In [3]:
#hide
df_mun = df.drop(["lat", "lon"], axis=1).set_index(["data", "municipio"]).groupby("municipio").cummax().reset_index()
df_mun["log_incidencia"] = np.log1p(df_mun["incidencia"])
df_mun["log_mortalidade"] = np.log1p(df_mun["mortalidade"])
df_mun = df_mun.query("suspeito > 0 or confirmado > 0 or morte > 0").sort_values("data")
df_maiores = df_mun.query(f"municipio in {localidades}")
ts_maiores = df_maiores.melt(id_vars=["municipio", "data"], var_name="métrica", 
                             value_name="valor", value_vars=["confirmado", "suspeito", "morte", "incidencia", "mortalidade"])

In [4]:
#hide 
dict_métrica = {
                 "suspeito": "Suspeitos",
                 "confirmado": "Confirmados",
                 "morte": "Mortes",
                 "incidencia": "Confirmados / 100 mil",
                 "mortalidade": "Mortes / 100 mil",
                }

ts_maiores["métrica"] = ts_maiores["métrica"].astype("category")
ts_maiores["métrica"] = ts_maiores["métrica"].cat.rename_categories(dict_métrica)

#### Estágio atual

##### Ranking dos municípios por métrica

In [5]:
#hide
idx_cols = ["municipio", "data", "codigo_ibge", "populacao_estimada_2019"]

df_base = df_mun.groupby("municipio").max().reset_index()
long_base = df_base.melt(id_vars=idx_cols, var_name="métrica", value_vars=["suspeito", "confirmado", "morte", "incidencia", "mortalidade"], value_name="valor")
long_largest = long_base.set_index(idx_cols + ["métrica"])["valor"].groupby("métrica").nlargest(10).reset_index(5, drop=True).reset_index()
long_largest["métrica"] = long_largest["métrica"].astype("category")
long_largest["métrica"] = long_largest["métrica"].cat.rename_categories(dict_métrica)

In [6]:
#hide_input
plotly_labels = {
                 "municipio": "Município",
                 "valor": "Valor",
                 "métrica": "Métrica",
                }
plotly_labels.update(dict_métrica)

po = px.bar(
       long_largest,
       y="municipio",
       x="valor",
       animation_frame="métrica",
       orientation="h",
       labels=plotly_labels,
       )

po.update_layout(
    updatemenus=[{"visible": False}],
)

#### Evolução

##### Acumulado de casos por dia

In [7]:
#hide_input
plotly_labels["data"] = "Data"

po = px.line(ts_maiores, 
             x="data", 
             y="valor", 
             animation_frame="métrica", 
             color="municipio",
             labels=plotly_labels)

po.update_layout(
    xaxis_tickformat = "%d/%m",
    yaxis_tickformat = "g",
    updatemenus=[{"visible": False}],
)

##### Acumulado de casos em dias desde o primeiro caso confirmado

In [8]:
#hide

# Computing day zero
df_maiores["data"] = pd.to_datetime(df_maiores["data"])
start_date = df_maiores.groupby("municipio")["data"].min().reset_index()
start_date.columns = ["municipio", "dia_zero"]

# Adding day zero to data
df_day0 = pd.merge(start_date, df_maiores)
days_elapsed = pd.to_datetime(df_day0["data"]) - pd.to_datetime(df_day0["dia_zero"])
df_day0["dias"] = days_elapsed.astype('timedelta64[D]')

# Transforming the data for plotting
ts_day0 = df_day0.melt(id_vars=["municipio", "dias"], var_name="métrica", 
                             value_name="valor", value_vars=["confirmado", "suspeito", "morte", "incidencia", "mortalidade"])

ts_day0["métrica"] = ts_day0["métrica"].astype("category")
ts_day0["métrica"] = ts_day0["métrica"].cat.rename_categories(dict_métrica)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [9]:
#hide_input
plotly_labels["dias"] = "Dias"

po = px.line(ts_day0, 
             x="dias", 
             y="valor", 
             animation_frame="métrica", 
             color="municipio",
             labels=plotly_labels)

po.update_layout(
    yaxis_tickformat = "g",
    updatemenus=[{"visible": False}],
)

#### Trajetória de dispersão pelo RN

##### Acumulado de casos confirmados

In [10]:
#hide
rn = requests.get("https://servicodados.ibge.gov.br/api/v2/malhas/24/?formato=application/vnd.geo+json&resolucao=5").json()
for location in rn['features']:
    location['id'] = location['properties']['codarea']

locations = requests.get("https://servicodados.ibge.gov.br/api/v1/localidades/estados/24/distritos").json()
location_list = [{
                  "codarea": municipio["municipio"]["id"],
                  "municipio": municipio["municipio"]["nome"]
                  }
                 for municipio in locations]

id_location = pd.DataFrame(location_list)   
id_location.loc[id_location["municipio"] == "Augusto Severo", "localidade"] = "Campo Grande"      
id_location.loc[id_location["municipio"] == "Januário Cicco", "localidade"] = "Boa Saúde"      

In [11]:
#hide
df_ch = pd.merge(df_mun, id_location)
df_confirmed = df_ch.query("confirmado > 0").sort_values("data")
df_confirmed["data"] = pd.to_datetime(df_confirmed["data"])
df_confirmed = df_confirmed.set_index("data").groupby("municipio").resample("W").max()
df_confirmed = df_confirmed.reset_index("data").sort_values("data")
df_deaths = df_confirmed.query("morte > 0").sort_values("data")
df_confirmed["data"] = df_confirmed["data"].dt.strftime("%d-%m")
df_deaths["data"] = df_deaths["data"].dt.strftime("%d-%m")

In [12]:
#hide_input

plotly_labels['log_incidencia'] = 'Incidência (log)'
plotly_labels["codarea"] = "Código do município (IBGE)"
plotly_labels.update(dict_métrica)

fig = px.choropleth(
                    df_confirmed,
                    geojson=rn, 
                    color="log_incidencia", 
                    locations="codarea", 
                    hover_name="municipio",
                    hover_data=["suspeito", "confirmado", "morte", "incidencia", "mortalidade"],
                    animation_frame="data",
                    center={"lat": -5.78362, "lon": -36.914},
                    color_continuous_scale='reds',
                    range_color=(0, df_ch["log_incidencia"].max()),
                    labels=plotly_labels,
                    )

fig.update_geos(projection={"scale": 70}, 
                fitbounds="locations", 
                visible=False,
                )

fig.update_layout(coloraxis_colorbar_title = "Máximo",
                  coloraxis_colorbar_showticklabels = False)

fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 1500

fig.show()

##### Acumulado de mortes

In [13]:
#hide_input

plotly_labels['log_mortalidade'] = 'Mortalidade (log)'

fig = px.choropleth(df_deaths,
                    geojson=rn, 
                    color="log_mortalidade", 
                    locations="codarea", 
                    hover_name="municipio",
                    hover_data=["suspeito", "confirmado", "morte", "incidencia", "mortalidade"],
                    animation_frame="data",
                    center={"lat": -5.78362, "lon": -36.914},
                    color_continuous_scale='reds',
                    range_color=(0, df_ch["log_mortalidade"].max()),
                    labels=plotly_labels,
                    )

fig.update_geos(projection={"scale": 70}, 
                fitbounds="locations", 
                visible=False,
                )

fig.update_layout(coloraxis_colorbar_title = "Máximo",
                  coloraxis_colorbar_showticklabels = False)

fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 1500

fig.show()